# 📊 Proyecto Guiado - Análisis de Ventas de Videojuegos
## Parte 5: Visualizaciones Avanzadas e Interactivas

---

### 🎯 Objetivos de este notebook:
1. Crear gráficos interactivos con Plotly
2. Desarrollar visualizaciones avanzadas
3. Construir dashboards visuales
4. Preparar visualizaciones para la app web
5. Aplicar storytelling con datos

---

### 📚 ¿Por qué Plotly?

**Plotly** permite crear gráficos interactivos:
- Zoom, pan, hover tooltips
- Exportables a HTML
- Perfectos para dashboards web
- Aspecto profesional y moderno

## 1. Importar librerías

In [ ]:
%pip install nbformat

In [2]:
# Importar librerías
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings

# Configuraciones
warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)

# Cargar dataset limpio
df = pd.read_csv('../data/vgsales_clean.csv')

print("✅ Dataset cargado")
print(f"📦 Dimensiones: {df.shape}")
print("\n🎨 Plotly cargado para gráficos interactivos")

✅ Dataset cargado
📦 Dimensiones: (16327, 19)

🎨 Plotly cargado para gráficos interactivos


---
## 2. Gráficos Básicos Interactivos

### 2.1 Top Juegos - Gráfico de Barras Interactivo

In [3]:
# Top 20 juegos más vendidos
top_juegos = df.nlargest(20, 'Global_Sales')[['Name', 'Platform', 'Year', 'Genre', 'Global_Sales']]

# Crear gráfico interactivo
fig = px.bar(top_juegos, 
             x='Global_Sales', 
             y='Name',
             orientation='h',
             title='Top 20 Videojuegos Más Vendidos de la Historia',
             labels={'Global_Sales': 'Ventas Globales (Millones)', 'Name': 'Juego'},
             color='Genre',
             hover_data=['Platform', 'Year'],
             color_discrete_sequence=px.colors.qualitative.Set3)

fig.update_layout(
    height=700,
    font=dict(size=11),
    title_font_size=18,
    hovermode='closest'
)

fig.show()

print("💡 Tip: Pasa el cursor sobre las barras para ver detalles. Puedes hacer zoom y exportar la imagen.")

💡 Tip: Pasa el cursor sobre las barras para ver detalles. Puedes hacer zoom y exportar la imagen.


### 2.2 Evolución Temporal Interactiva

In [4]:
# Ventas por año y región
ventas_tiempo = df.groupby('Year')[['NA_Sales', 'EU_Sales', 'JP_Sales', 'Other_Sales']].sum().reset_index()

# Crear gráfico de líneas interactivo
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=ventas_tiempo['Year'], y=ventas_tiempo['NA_Sales'],
    name='Norteamérica',
    mode='lines+markers',
    line=dict(color='#3498db', width=3),
    marker=dict(size=6)
))

fig.add_trace(go.Scatter(
    x=ventas_tiempo['Year'], y=ventas_tiempo['EU_Sales'],
    name='Europa',
    mode='lines+markers',
    line=dict(color='#2ecc71', width=3),
    marker=dict(size=6)
))

fig.add_trace(go.Scatter(
    x=ventas_tiempo['Year'], y=ventas_tiempo['JP_Sales'],
    name='Japón',
    mode='lines+markers',
    line=dict(color='#e74c3c', width=3),
    marker=dict(size=6)
))

fig.add_trace(go.Scatter(
    x=ventas_tiempo['Year'], y=ventas_tiempo['Other_Sales'],
    name='Otros',
    mode='lines+markers',
    line=dict(color='#f39c12', width=3),
    marker=dict(size=6)
))

fig.update_layout(
    title='Evolución de Ventas por Región (1980-2020)',
    xaxis_title='Año',
    yaxis_title='Ventas (Millones)',
    hovermode='x unified',
    height=600,
    font=dict(size=12),
    legend=dict(x=0.02, y=0.98, bgcolor='rgba(255,255,255,0.8)')
)

fig.show()

---
## 3. Gráficos de Distribución

### 3.1 Sunburst Chart - Jerarquía de Géneros y Plataformas

In [5]:
# Preparar datos agregados para sunburst
genero_plat = df.groupby(['Genre', 'Platform_Type'])['Global_Sales'].sum().reset_index()

# Crear sunburst chart
fig = px.sunburst(
    genero_plat,
    path=['Genre', 'Platform_Type'],
    values='Global_Sales',
    title='Distribución de Ventas: Género → Tipo de Plataforma',
    color='Global_Sales',
    color_continuous_scale='RdYlGn',
    height=700
)

fig.update_traces(textinfo='label+percent parent')
fig.show()

print("💡 Haz clic en las secciones para explorar la jerarquía")

💡 Haz clic en las secciones para explorar la jerarquía


### 3.2 Treemap - Ventas por Publisher y Género

In [6]:
# Top publishers con sus géneros
top_publishers = df['Publisher'].value_counts().head(10).index
df_top_pub = df[df['Publisher'].isin(top_publishers)]

pub_genre = df_top_pub.groupby(['Publisher', 'Genre'])['Global_Sales'].sum().reset_index()

# Crear treemap
fig = px.treemap(
    pub_genre,
    path=['Publisher', 'Genre'],
    values='Global_Sales',
    title='Ventas por Publisher y Género (Top 10 Publishers)',
    color='Global_Sales',
    color_continuous_scale='Viridis',
    height=700
)

fig.update_traces(textinfo='label+value')
fig.show()

---
## 4. Análisis Comparativo

### 4.1 Box Plot Interactivo - Ventas por Género

In [7]:
# Box plot de ventas por género
fig = px.box(
    df,
    x='Genre',
    y='Global_Sales',
    title='Distribución de Ventas por Género',
    color='Genre',
    points='outliers',  # Mostrar outliers
    hover_data=['Name', 'Platform', 'Year'],
    height=600
)

fig.update_layout(
    xaxis_title='Género',
    yaxis_title='Ventas Globales (Millones)',
    showlegend=False,
    font=dict(size=11)
)

fig.show()

### 4.2 Violin Plot - Comparación de Regiones

In [8]:
# Preparar datos en formato long para violin plot
df_long = pd.melt(
    df,
    id_vars=['Name', 'Genre'],
    value_vars=['NA_Sales', 'EU_Sales', 'JP_Sales', 'Other_Sales'],
    var_name='Region',
    value_name='Sales'
)

# Renombrar regiones
df_long['Region'] = df_long['Region'].map({
    'NA_Sales': 'Norteamérica',
    'EU_Sales': 'Europa',
    'JP_Sales': 'Japón',
    'Other_Sales': 'Otros'
})

# Crear violin plot
fig = px.violin(
    df_long,
    x='Region',
    y='Sales',
    title='Distribución de Ventas por Región (Violin Plot)',
    color='Region',
    box=True,  # Incluir box plot dentro
    points='outliers',
    height=600,
    color_discrete_map={
        'Norteamérica': '#3498db',
        'Europa': '#2ecc71',
        'Japón': '#e74c3c',
        'Otros': '#f39c12'
    }
)

fig.update_layout(
    yaxis_title='Ventas (Millones)',
    showlegend=False
)

fig.show()

print("💡 El violin plot muestra la densidad de la distribución")

💡 El violin plot muestra la densidad de la distribución


---
## 5. Análisis Multivariable

### 5.1 Scatter Plot 3D - Año, Ventas y Género

In [9]:
# Muestra de datos para mejor visualización 3D
df_sample = df.sample(1000, random_state=42)

# Gráfico 3D
fig = px.scatter_3d(
    df_sample,
    x='NA_Sales',
    y='EU_Sales',
    z='JP_Sales',
    color='Genre',
    size='Global_Sales',
    hover_name='Name',
    hover_data=['Year', 'Platform'],
    title='Análisis 3D: Ventas por Región y Género (Muestra de 1000 juegos)',
    labels={
        'NA_Sales': 'Ventas NA (M)',
        'EU_Sales': 'Ventas EU (M)',
        'JP_Sales': 'Ventas JP (M)'
    },
    height=700
)

fig.update_traces(marker=dict(line=dict(width=0.5, color='DarkSlateGrey')))
fig.show()

print("💡 Usa el mouse para rotar el gráfico 3D")

💡 Usa el mouse para rotar el gráfico 3D


### 5.2 Bubble Chart - Plataformas por Año y Ventas

In [10]:
# Agrupar por plataforma y año
plat_year = df.groupby(['Platform', 'Year']).agg({
    'Global_Sales': 'sum',
    'Name': 'count'
}).reset_index()
plat_year.columns = ['Platform', 'Year', 'Total_Sales', 'Game_Count']

# Top 10 plataformas para claridad
top_platforms = df.groupby('Platform')['Global_Sales'].sum().nlargest(10).index
plat_year_top = plat_year[plat_year['Platform'].isin(top_platforms)]

# Bubble chart
fig = px.scatter(
    plat_year_top,
    x='Year',
    y='Total_Sales',
    size='Game_Count',
    color='Platform',
    title='Evolución de Plataformas: Año vs Ventas (Top 10 Plataformas)',
    labels={
        'Year': 'Año',
        'Total_Sales': 'Ventas Totales (Millones)',
        'Game_Count': 'Cantidad de Juegos'
    },
    hover_data=['Game_Count'],
    height=600,
    size_max=60
)

fig.update_layout(
    font=dict(size=11),
    legend=dict(x=1.05, y=1)
)

fig.show()

---
## 6. Heatmaps Interactivos

### 6.1 Heatmap - Ventas por Género y Década

In [11]:
# Crear pivot table
genre_decade = df.pivot_table(
    values='Global_Sales',
    index='Genre',
    columns='Decade',
    aggfunc='sum',
    fill_value=0
).round(2)

# Crear heatmap interactivo
fig = go.Figure(data=go.Heatmap(
    z=genre_decade.values,
    x=genre_decade.columns,
    y=genre_decade.index,
    colorscale='YlOrRd',
    text=genre_decade.values,
    texttemplate='%{text:.0f}M',
    textfont={"size": 10},
    hoverongaps=False,
    colorbar=dict(title="Ventas (M)")
))

fig.update_layout(
    title='Heatmap: Ventas por Género y Década',
    xaxis_title='Década',
    yaxis_title='Género',
    height=600,
    font=dict(size=11)
)

fig.show()

### 6.2 Heatmap - Preferencias de Género por Región

In [12]:
# Ventas por género en cada región
genre_region = df.groupby('Genre')[['NA_Sales', 'EU_Sales', 'JP_Sales', 'Other_Sales']].sum()

# Normalizar por región (porcentaje)
genre_region_pct = genre_region.div(genre_region.sum(axis=0), axis=1) * 100

# Renombrar columnas
genre_region_pct.columns = ['Norteamérica', 'Europa', 'Japón', 'Otros']

# Crear heatmap
fig = go.Figure(data=go.Heatmap(
    z=genre_region_pct.values,
    x=genre_region_pct.columns,
    y=genre_region_pct.index,
    colorscale='Viridis',
    text=genre_region_pct.values,
    texttemplate='%{text:.1f}%',
    textfont={"size": 10},
    colorbar=dict(title="Porcentaje")
))

fig.update_layout(
    title='Preferencias de Género por Región (%)',
    xaxis_title='Región',
    yaxis_title='Género',
    height=600,
    font=dict(size=11)
)

fig.show()

print("💡 Los colores más claros indican mayor preferencia en esa región")

💡 Los colores más claros indican mayor preferencia en esa región


---
## 7. Dashboard Consolidado

### 7.1 Panel de Métricas Clave

In [13]:
# Calcular métricas clave
total_juegos = len(df)
total_ventas = df['Global_Sales'].sum()
promedio_ventas = df['Global_Sales'].mean()
top_genero = df.groupby('Genre')['Global_Sales'].sum().idxmax()
top_plataforma = df.groupby('Platform')['Global_Sales'].sum().idxmax()
top_publisher = df.groupby('Publisher')['Global_Sales'].sum().idxmax()

# Crear subplots para dashboard
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=(
        'Ventas por Región',
        'Top 10 Géneros',
        'Evolución Temporal',
        'Top 10 Plataformas',
        'Distribución de Categorías',
        'Top 10 Publishers'
    ),
    specs=[
        [{'type': 'bar'}, {'type': 'bar'}, {'type': 'scatter'}],
        [{'type': 'bar'}, {'type': 'pie'}, {'type': 'bar'}]
    ],
    vertical_spacing=0.15,
    horizontal_spacing=0.1
)

# 1. Ventas por región
regiones = ['NA', 'EU', 'JP', 'Otros']
ventas_region = [df['NA_Sales'].sum(), df['EU_Sales'].sum(), 
                 df['JP_Sales'].sum(), df['Other_Sales'].sum()]
fig.add_trace(
    go.Bar(x=regiones, y=ventas_region, marker_color=['#3498db', '#2ecc71', '#e74c3c', '#f39c12']),
    row=1, col=1
)

# 2. Top géneros
top_genres = df.groupby('Genre')['Global_Sales'].sum().nlargest(10).sort_values()
fig.add_trace(
    go.Bar(x=top_genres.values, y=top_genres.index, orientation='h', marker_color='#9b59b6'),
    row=1, col=2
)

# 3. Evolución temporal
ventas_year = df.groupby('Year')['Global_Sales'].sum()
fig.add_trace(
    go.Scatter(x=ventas_year.index, y=ventas_year.values, mode='lines', 
               line=dict(color='#e74c3c', width=2), fill='tozeroy'),
    row=1, col=3
)

# 4. Top plataformas
top_plat = df.groupby('Platform')['Global_Sales'].sum().nlargest(10).sort_values()
fig.add_trace(
    go.Bar(x=top_plat.values, y=top_plat.index, orientation='h', marker_color='#1abc9c'),
    row=2, col=1
)

# 5. Categorías de ventas
cat_counts = df['Sales_Category'].value_counts()
fig.add_trace(
    go.Pie(labels=cat_counts.index, values=cat_counts.values, 
           marker=dict(colors=['#95a5a6', '#3498db', '#2ecc71', '#f39c12'])),
    row=2, col=2
)

# 6. Top publishers
top_pub = df.groupby('Publisher')['Global_Sales'].sum().nlargest(10).sort_values()
fig.add_trace(
    go.Bar(x=top_pub.values, y=top_pub.index, orientation='h', marker_color='#d35400'),
    row=2, col=3
)

# Layout general
fig.update_layout(
    title_text=f"📊 Dashboard de Análisis de Videojuegos<br><sub>{total_juegos:,} juegos | {total_ventas:.0f}M ventas totales | Promedio: {promedio_ventas:.2f}M</sub>",
    showlegend=False,
    height=900,
    font=dict(size=10)
)

fig.show()

print("\n📊 RESUMEN EJECUTIVO")
print("=" * 80)
print(f"Total de Juegos: {total_juegos:,}")
print(f"Ventas Totales: {total_ventas:,.0f} millones")
print(f"Promedio de Ventas: {promedio_ventas:.2f} millones")
print(f"\nTop Género: {top_genero}")
print(f"Top Plataforma: {top_plataforma}")
print(f"Top Publisher: {top_publisher}")


📊 RESUMEN EJECUTIVO
Total de Juegos: 16,327
Ventas Totales: 8,820 millones
Promedio de Ventas: 0.54 millones

Top Género: Action
Top Plataforma: PS2
Top Publisher: Nintendo


---
## 8. Animaciones

### 8.1 Gráfico Animado - Evolución de Géneros por Año

In [14]:
# Preparar datos para animación
genre_year_anim = df.groupby(['Year', 'Genre'])['Global_Sales'].sum().reset_index()

# Solo años con buenos datos (1990-2016)
genre_year_anim = genre_year_anim[(genre_year_anim['Year'] >= 1990) & (genre_year_anim['Year'] <= 2016)]

# Crear gráfico animado
fig = px.bar(
    genre_year_anim,
    x='Genre',
    y='Global_Sales',
    animation_frame='Year',
    animation_group='Genre',
    color='Genre',
    title='Evolución de Ventas por Género (1990-2016)',
    labels={'Global_Sales': 'Ventas (Millones)'},
    range_y=[0, genre_year_anim['Global_Sales'].max() * 1.1],
    height=600
)

fig.update_layout(
    showlegend=False,
    xaxis_title='Género',
    yaxis_title='Ventas Globales (Millones)'
)

fig.show()

print("💡 Presiona 'Play' para ver la evolución año a año")

💡 Presiona 'Play' para ver la evolución año a año


---
## ✅ Resumen Final

### 🎨 Visualizaciones Creadas:

1. ✅ **Gráficos Básicos Interactivos**
   - Top juegos (barras horizontales)
   - Evolución temporal (líneas múltiples)

2. ✅ **Gráficos de Distribución**
   - Sunburst (jerarquía género-plataforma)
   - Treemap (publisher-género)

3. ✅ **Análisis Comparativo**
   - Box plots por género
   - Violin plots por región

4. ✅ **Análisis Multivariable**
   - Scatter 3D (ventas regionales)
   - Bubble chart (plataformas temporales)

5. ✅ **Heatmaps**
   - Género x Década
   - Género x Región

6. ✅ **Dashboard Consolidado**
   - 6 visualizaciones en un panel
   - Métricas clave

7. ✅ **Animaciones**
   - Evolución de géneros por año

---

### 🎯 Aplicación Web:

Estas visualizaciones serán la base para la aplicación Streamlit.

**Próximos pasos:**
1. Crear app de Streamlit con estas visualizaciones
2. Añadir filtros interactivos
3. Implementar múltiples páginas
4. Exportar visualizaciones

---

### 💡 Consejos para la Clase:

**Para estudiantes principiantes:**
- Empezar con gráficos simples (barras, líneas)
- Entender los parámetros básicos
- Practicar con diferentes datasets

**Para estudiantes avanzados:**
- Experimentar con layouts complejos
- Crear dashboards personalizados
- Combinar múltiples fuentes de datos

---

### 📚 Recursos Adicionales:

- [Plotly Documentation](https://plotly.com/python/)
- [Plotly Express](https://plotly.com/python/plotly-express/)
- [Streamlit Gallery](https://streamlit.io/gallery)

---

**¡Notebooks completados! 🎉**

Ahora tenemos:
1. ✅ Introducción y carga de datos
2. ✅ Exploración inicial (EDA)
3. ✅ Limpieza y preparación
4. ✅ Análisis estadístico avanzado
5. ✅ Visualizaciones avanzadas

**Siguiente paso: Crear la aplicación web con Streamlit** 🚀